In [1]:
from pandas import DataFrame, read_csv
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd 
import sys
import matplotlib 
from pandas import ExcelWriter
import datetime

import os
import xlwt
from xlwt.Workbook import *
from pandas import ExcelWriter
import xlsxwriter

def timevalue_money(t, v): #inflation data https://www.imf.org/external/datamapper/PCPIPCH@WEO/OEMDC/ADVEC/WEOWORLD
    difference = 2019 - t
    return v*(1+0.036)**(difference)

In [2]:

original_data = pd.ExcelFile('crunchbase_export.xlsx') #importing whole dataset

In [3]:
all_funded_companies = pd.read_excel(original_data, 1) #importing data page by page
all_rounds= pd.read_excel(original_data, 2)
all_investors = pd.read_excel(original_data, 3)
all_acquis = pd.read_excel(original_data, 4)
all_ipos = pd.read_excel(original_data, 5) 


In [ ]:
top_VCPE = pd.ExcelFile('top_VC_and_PE_firms.xlsx') #importing VC and PE
topVC = pd.read_excel(top_VCPE, 4) #importing VC data first page
topPE = pd.read_excel(top_VCPE, 0) #importing PE dat second page
topCVC = pd.read_excel(top_VCPE, 2)


In [4]:
#Filter according to labels
descriptions_list = all_funded_companies['category_group_list'] #create a Series of descriptions
#labels= ['energy', 'sustainable', 'sustainability', 'renewable', 'carbon']

label_energy = 'energy' #create label to look for
label_sust = 'sustainability'
#label_oil = 'oil'

energy_companies_indices_in = [all_funded_companies['category_group_list'].index[i] for i, j in enumerate(descriptions_list) if label_energy.casefold() in str(j).casefold()]# or label_sust.casefold() in str(j).casefold()]
#sust_companies_indices_in = [all_funded_companies['category_group_list'].index[i] for i, j in enumerate(descriptions_list) if label_sust.casefold() in str(j).casefold()]

#Retrieve indices of those companies which have the label energy in their short description
#casefold is applied to avoid case sensitivity
energy_companies_in = all_funded_companies.loc[energy_companies_indices_in] #Create a new dataframe with all energy companies

#If in need to filter out a certain condition uncomment:
#energy_companies_indices_out = [energy_companies_in.index[i] for i, j in enumerate(energy_companies_in['short_description']) if label_oil.casefold() in str(j).casefold()]
#energy_companies = energy_companies_in.drop(energy_companies_indices_out) 
len(energy_companies_in)

9162

In [5]:
#check which companies don't have founding date and set to 1000-1-1 (yyyy/m/d) 
energy_companies_with_fd = energy_companies_in ##WORKING ON A DIFFERENT DATASET

for m in energy_companies_indices_in:  #for every energy company index 
    if str(energy_companies_with_fd['founded_on'].loc[m]) == 'nan': # check which ones have no founding date i.e. 'nan'
        energy_companies_with_fd.at[m,'founded_on'] = datetime.date(1000,1,1) #change nan for date object 1000(yr) Jan 1st
        
    else:
        energy_companies_with_fd.at[m,'founded_on'] = datetime.datetime.strptime(energy_companies_with_fd['founded_on'].loc[m], '%Y-%M-%d').date() 
        #if it has date do nothing
#energy_companies_in = None

In [6]:
#Filtering data from a certain year 
numb_years_analysis = 5
limit_date = datetime.date.today().year - numb_years_analysis #year limit, all companies founded before are filtered out
energy_filtered_date = energy_companies_with_fd # new dataframe creation
indices_old_companies = [] #indices of all old companies
#upper_limit = 200X

for m in energy_companies_indices_in: 
    if energy_companies_with_fd['founded_on'].loc[m].year < limit_date:# or energy_companies_with_fd['founded_on'].loc[m].year > upper_limit:  #compare founding year to limit
        indices_old_companies.append(m) #create an array of indices of companies founded previously to the limit 
    else:
        continue
        
energy_filtered_date = energy_filtered_date.drop(indices_old_companies) 
#remove the rows associated to the old indices.  
#energy_companies_with_fd = None

In [38]:
len(energy_filtered_date)

1061

In [7]:
all_rounds
#Filter according to label energy as previously defined
category_list = all_rounds['company_category_list'] #create a Series of just the categories 
#possible labels to keep in mind = ['energy', 'sustainable', 'sustainability', 'renewable', 'carbon']


rounds_energy_companies_indices = [category_list.index[i] for i, j in enumerate(category_list) if label_energy.casefold() in str(j).casefold()]# or label_sust in str(j)]
#Retrieve indices of those companies which have the label energy in their short description
#casefold is applied to avoid case sensitivity
rounds_energy_companies = all_rounds.loc[rounds_energy_companies_indices] #Create a new dataframe with all energy companies

#convert string dates to date objects:
for m in rounds_energy_companies_indices: #for every energy company index 
       rounds_energy_companies.at[m,'announced_on'] = datetime.datetime.strptime(rounds_energy_companies['announced_on'].loc[m], '%Y-%M-%d').date()
        #change nan for date object 1000(yr) Jan 1st
        
#filter by date: there's no real need for this step, as the date filter is already applied in the companies selection, 
#even though, doing so will increase the efficiency of the process

#use same limit as defined before, i.e. numb_years_analysis
rounds_energy_filtered_date = rounds_energy_companies #new dataframe creation
rounds_indices_old_companies = [] #indices of all old companies

for m in rounds_energy_companies_indices: 
    if rounds_energy_companies['announced_on'].loc[m].year < limit_date:  #compare founding year to limit
        rounds_indices_old_companies.append(m) #create an array of indices of companies founded previously to the limit 
    else:
        continue
        
rounds_energy_filtered_date = rounds_energy_filtered_date.drop(rounds_indices_old_companies) 
#remove the rows associated to the old indices.  
 

In [44]:
#identify which companies present rounds in the second data sheet; localise index of such companies and respective rounds

indices_of_energy_companies_with_rounds = [] #at which point in the first file are they located 
indices_of_rounds_location = [] #at which point in the second file are they located

for first_index, comp_name_from_first_page in enumerate(energy_filtered_date['company_name']): #0,1,2,... name1 name2
    for second_index, comp_name_from_second_page in enumerate(rounds_energy_filtered_date['company_name']): #0,1,2,... name1 name2

        if str(comp_name_from_first_page).casefold() == str(comp_name_from_second_page).casefold(): #if same names
            indices_of_energy_companies_with_rounds.append(energy_filtered_date['company_name'].index[first_index]) #keep index of company in first sheet
            indices_of_rounds_location.append(rounds_energy_filtered_date['company_name'].index[second_index]) #keep indices of round in second sheet 
            # note that if company has more than one round: e.g. indices with rounds = (36, 36, 36...) 
            # indices of rounds = (126, 136, 789,...) i.e. company 36 has three rounds locate in these positions in sheet 2
        else:
            pass
#if an indice is not in the set of companies with rounds, it obv has no rounds
indices_of_energy_companies_WITHOUT_rounds = [i for i in energy_filtered_date.index if i not in indices_of_energy_companies_with_rounds]
#eliminate the ones without rounds
energy_companies_filtered_bydate_with_rounds = energy_filtered_date.drop(indices_of_energy_companies_WITHOUT_rounds)

#elimante rounds associated to companies outside of the dataset
indices_of_rounds_WITHOUT_company = [ i for i in rounds_energy_filtered_date.index if i not in indices_of_rounds_location]
rounds_corresponding = rounds_energy_filtered_date.drop(indices_of_rounds_WITHOUT_company)

#list of indices of companies that say they have more than 0 rounds but don't appear in rounds sheet
#onesitos = [inx for inx, numb in enumerate(energy_filtered_date['funding_rounds']) if numb > 0 and inx  in indices_of_energy_companies_WITHOUT_rounds]

In [54]:
#Filtering by rounds type
#Accepted rounds
accepted_rounds = ['corporate_round','series_a','series_b','series_c','seed','pre_seed','private_equity','series_unknown','convertible_note']
#Object where to save accepted rounds indices
indices_VCrounds = []


for indexs, round_type in enumerate(rounds_corresponding['funding_round_type']): #0,1,2,... type1, type2...
#if the type of the round is in the list of acepted ones, we keep it
    if str(round_type).casefold() in accepted_rounds: 
        #save it into the object
            indices_VCrounds.append(rounds_corresponding['funding_round_type'].index[indexs]) #keep index of company in first sheet
            
    else:
        pass
#if an indice of the initial dataframe is not in the new object, means it wasn't an acceptd round
indices_of_NONVCrounds = [ i for i in rounds_corresponding.index if i not in indices_VCrounds]
#new dataframe with only VC rounds
VCrounds_corresponding = rounds_corresponding.drop(indices_of_NONVCrounds)
VCrounds_corresponding

company_name country_code state_code  \
102                                        Electron          GBR        NaN   
129                                    Solar Monkey          NLD        NaN   
235                                        Ferntech          DEU        NaN   
287                            Zaphiro Technologies          CHE        NaN   
306                         Earth Science Analytics          NOR        NaN   
662                                            Nesh          NaN        NaN   
1172                                      CycloPure          USA         CA   
1211                               Revere Resources          USA         TX   
1235                                  Zenobe Energy          GBR        NaN   
1373                               Dandelion Energy          USA         NY   
1417                                   Tank Utility          USA         MA   
1492                                   Tonik Energy          GBR        NaN   
2055                                          ARROE          GBR        NaN   
2191                                        EnergyX          CAN         ON   
2327                                          RigUp          USA         TX   
2328                                          Rovco          GBR        NaN   
2412                             Yellow Door Energy          ARE        NaN   
2414                                       ZerO Box          CHN        NaN   
2706                                      Flexciton          GBR        NaN   
2992                           Daphne Technology SA          CHE        NaN   
3266                                     TemperPack          USA         VA   
3271                                   Trawell Data          USA         NY   
3298                            Discovery Midstream          USA         TX   
3382                                           Nowi          NLD        NaN   
3480                                       TresMoto          IND        NaN   
3541                                      Northvolt          SWE        NaN   
3612                       Solar Earth Technologies          CAN         BC   
3733                                       Hometree          GBR        NaN   
3774                                       Q Energy          GBR        NaN   
3823                                    Alva Motors          DEU        NaN   
...                                             ...          ...        ...   
141371                                   Kraftblock          DEU        NaN   
141526                                     PowiDian          FRA        NaN   
142108                                      Servato          USA         LA   
142462                           Pelican Renewables          USA         NY   
143804                                    CoControl          GBR        NaN   
144313                             RiverRock Energy          USA         TX   
144362                                   PingThings          USA         CA   
144683  Sustainable Energy & Agriculture Technology          USA         AZ   
144770                      Superior Solar Solution          USA         CA   
144977                                      Nativus          USA         NV   
145832                  Shift Energy Holdings, Inc.          USA         CA   
145941                                Zolair Energy          CAN         BC   
147354                         EDF Store & Forecast          FRA        NaN   
147555                                       Seneco          DNK        NaN   
148726                         Park Energy Services          USA         OK   
149220                           Tall Oak Midstream          USA         OK   
149369                         Arctic Power Berries          GBR        NaN   
149623                                      PetroDE          USA         CO   
149766                                        10Six          USA         NY   
149799    

In [ ]:
#as before but just for VC rounds

indices_of_energy_companies_with_VCrounds = [] #at which point in the first file are they located 

for first_index, comp_name_from_first_page in enumerate(energy_filtered_date['company_name']): #0,1,2,... name1 name2
    for second_index, comp_name_from_second_page in enumerate(VCrounds_corresponding['company_name']): #0,1,2,... name1 name2

        if str(comp_name_from_first_page).casefold() == str(comp_name_from_second_page).casefold(): #if same names
            indices_of_energy_companies_with_VCrounds.append(energy_filtered_date['company_name'].index[first_index]) #keep index of company in first sheet
        else:
            pass
#if an indice is not in the set of companies with rounds, it obv has no rounds
indices_of_energy_companies_WITHOUTVC_rounds = [i for i in energy_filtered_date.index if i not in indices_of_energy_companies_with_VCrounds]
#eliminate the ones without rounds
energy_companies_filtered_bydate_with_rounds = energy_filtered_date.drop(indices_of_energy_companies_WITHOUT_rounds)


#list of indices of companies that say they have more than 0 rounds but don't appear in rounds sheet
#onesitos = [inx for inx, numb in enumerate(energy_filtered_date['funding_rounds']) if numb > 0 and inx  in indices_of_energy_companies_WITHOUT_rounds]

In [35]:
#Number of rounds with no money value
sum([1 for i in rounds_corresponding['raised_amount_usd'] if str(i).casefold() == 'nan'])

397

In [53]:
#exporting to csv
#energy_companies_filtered_bydate_with_rounds.to_csv(r'Export.csv')

writer = pd.ExcelWriter('export.xlsx', engine='xlsxwriter')

# Write each dataframe to a different worksheet.
energy_companies_filtered_bydate_with_rounds.to_excel(writer, sheet_name='Founded')
VCrounds_corresponding.to_excel(writer, sheet_name='Rounds')

all_acquis.to_excel(writer, sheet_name='Acq')
all_ipos.to_excel(writer, sheet_name='Ipos')


# Close the Pandas Excel writer and output the Excel file.
writer.save()


C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/grubby-games' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/idt' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/kawan-group-s-a-s' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/netxen' since it exceeds Excel's limit of 65,530 URLS per worksh

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/periculum-services-group' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/standard-oilfield-services' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/verisoft-infosystems-private-ltd' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/b-v-consultant

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/er-consultants' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/hand-prod-sp-z-o-o' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/kerr-nelson' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/maps-a-la-carte' since it exceeds Excel's limit of 65

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/nuvonyx' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/these-days' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/truck-center-hauser' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/wg-group' since it exceeds Excel's limit of 65,530 URLS per 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/bb-biotech-ag' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/luma-2' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/read

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/unit4' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/avolon-holdings' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/webuildapps' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/gp-strategies' since it exceeds Excel's limit of 65,530 URLS per 

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/celldex-therapeutics' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/vericlaim' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/black-diamond-group' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/drop-out-club' since it exceeds Excel's limit of

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/energy-fuels' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/gaia-smart-cities' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/tablelist' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/fluent-inc' since it exceeds Excel's limit of 65,530 URLS 

C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/geocomm' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/aminolabs' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/halo-business-intelligence' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\ProgramData\Anaconda3\lib\site-packages\xlsxwriter\worksheet.py:918: UserWarning: Ignoring URL 'https://www.crunchbase.com/organization/fantasia-holdings-group-co-ltd' since it exceeds Excel

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
#keeping only rounds that correspond to an A round
Aonly_rounds_energy_date = rounds_energy_filtered_date #copy dataframe
non_Arounds = list() #create list of indices of such companies
for ind, name in enumerate(Aonly_rounds_energy_date['funding_round_type']):
    if str(name).casefold() != 'series_a': #if not series a
        non_Arounds.append(Aonly_rounds_energy_date.index[ind]) #get index of the round so it can be removed at the end
    else:# do nothing
        continue

Aonly_rounds_energy_date = Aonly_rounds_energy_date.drop(non_Arounds) # drop rounds != A round
#companies that present more than one A round


In [ ]:
#retrieve indices of rounds of companies at least one top VCPE
indices_in_rounds_of_companies_topVC_PE_backed = [] 
#list of indices in the rounds file of the companies with at least one top VC PE

    #VC SECTION
for m in set(topVC['Top 100 VC companies']): # taking the names (m) of each VC in the list
    for j in range(0,len(rounds_energy_filtered_date['investor_names'])): # running through all rounds 
        if str(m).casefold() in str(rounds_energy_filtered_date['investor_names'].iloc[j]).casefold() and rounds_energy_filtered_date['investor_names'].index[j] not in indices_in_rounds_of_companies_topVC_PE_backed: 
        #if match, and not already in the list, append
            indices_in_rounds_of_companies_topVC_PE_backed.append(rounds_energy_filtered_date['investor_names'].index[j])
        else: # no match or already in the list, do nothing
            continue

counter = []  
    #CVC SECTION
for m in topCVC['Green CVC']: #same for CVC
       for j in range(0,len(rounds_energy_filtered_date['investor_names'])):
        if str(m).casefold() in str(rounds_energy_filtered_date['investor_names'].iloc[j]).casefold():# and rounds_energy_filtered_date['investor_names'].index[j] not in indices_in_rounds_of_companies_topVC_PE_backed:
            counter.append(m)
            indices_in_rounds_of_companies_topVC_PE_backed.append(rounds_energy_filtered_date['investor_names'].index[j])
        else:
            continue

    
    
    
    #PE SECTION
#for m in topPE['Top 100 VC companies']: #same for PE
 #      for j in range(0,len(rounds_energy_filtered_date['investor_names'])):
  #      if str(m).casefold() in str(rounds_energy_filtered_date['investor_names'].iloc[j]).casefold() and rounds_energy_filtered_date['investor_names'].index[j] not in indices_in_rounds_of_companies_topVC_PE_backed:
   #         indices_in_rounds_of_companies_topVC_PE_backed.append(rounds_energy_filtered_date['investor_names'].index[j])
    #    else:
     #       continue


In [ ]:
#from indices to names to undercover repetitions
names_top_backed = set(rounds_energy_filtered_date['company_name'].loc[indices_in_rounds_of_companies_topVC_PE_backed])
#using set to remove repetitions, names_top_backed are the names of companies with at least 1 round with at least 1 top VCPE

topVCPE_backed = pd.DataFrame()
main_indices_of_VCPE_energy_companies = list()

for m in names_top_backed: #taking each name of company in the list
    for j in range(0,len(energy_filtered_date)): # thorough all energy companies that have rounds
        if str(m).casefold() == str(energy_filtered_date['company_name'].iloc[j]).casefold():
            #if match in name, copy company's idnex in list
            main_indices_of_VCPE_energy_companies.append(energy_filtered_date.index[j])
        else: #no match, do nothing
            continue


In [ ]:
len(main_indices_of_VCPE_energy_companies)


In [ ]:
#new dataframe with companies energy, date, rounds and top backed
energy_date_rounds_topVCPE = energy_companies_filtered_bydate_with_rounds.loc[main_indices_of_VCPE_energy_companies]  
#keep only those companies 
energy_date_rounds_topVCPE = energy_date_rounds_topVCPE.sort_index(ascending=True) #sorting by index
energy_date_rounds_topVCPE#these are the ones present both in the first and second sheet 

In [ ]:
#counting acquisitions
a=0

for first_index, comp_name_from_first_page in enumerate(energy_filtered_date['company_name'][main_indices_of_VCPE_energy_companies]): #0,1,2,... name1 name2
    for second_index, comp_name_from_second_page in enumerate(all_acquis['acquiree_name']): #0,1,2,... name1 name2

        if str(comp_name_from_first_page).casefold() == str(comp_name_from_second_page).casefold(): #if same names
            print(comp_name_from_first_page)
            a += 1 #keep indices of round in second sheet 
            # note that if company has more than one round: e.g. indices with rounds = (36, 36, 36...) 
            # indices of rounds = (126, 136, 789,...) i.e. company 36 has three rounds locate in these positions in sheet 2
        else:
            pass
#if an indice is not in the set of companies with rounds, it obv has no rounds
print('Number of acquisitions is {}.'.format(a))


In [ ]:
#counting IPOs of top VCPE
a=0

for first_index, comp_name_from_first_page in enumerate(energy_filtered_date['company_name'][main_indices_of_VCPE_energy_companies]): #0,1,2,... name1 name2
    for second_index, comp_name_from_second_page in enumerate(all_ipos['name']): #0,1,2,... name1 name2

        if str(comp_name_from_first_page).casefold() == str(comp_name_from_second_page).casefold(): #if same names
            a += 1 #keep indices of round in second sheet 
            print(comp_name_from_first_page)
            # note that if company has more than one round: e.g. indices with rounds = (36, 36, 36...) 
            # indices of rounds = (126, 136, 789,...) i.e. company 36 has three rounds locate in these positions in sheet 2
        else:
            pass
#if an indice is not in the set of companies with rounds, it obv has no rounds
print('Number of IPOs is {}.'.format(a))


In [ ]:
#number of rounds of energy companies founded in the last 10 years that don't belong to any energy company 
#founded in the last 10 years  appearing in the first sheet 
strings = [str(j).casefold() for j in list(energy_filtered_date['company_name'])]
sum([1 for i in rounds_energy_filtered_date['company_name'] if str(i).casefold() not in strings])


In [ ]:
#Looking for how many companies were founded in a certain country:
#countries = ['BEL','BGR','CZE','DNK','DEU','EST','IRL','GRC','ESP','FRA','HRV','ITA','CYP','LVA','LTU','LUX','HUN','MLT','NLD','AUT','POL','PRT','ROM','SLV','SVK','FIN','SWE','GBR']
countries = ['GBR']
number_of_eu_companies = sum([1 for i, j in enumerate(energy_filtered_date['country_code']) if str(j) in countries])
number_of_eu_companies
#and in percenatge...
#number_of_british_companies/len(energy_filtered_date) *100

In [ ]:
#counting acq. by status
a=0

for j, m in enumerate(energy_filtered_date['status'][main_indices_of_VCPE_energy_companies]): #0,1,2,... name1 name2
    if str(m).casefold() == 'acquired'.casefold():
        print(energy_filtered_date['company_name'].loc[energy_filtered_date['status'][main_indices_of_VCPE_energy_companies].index[j]])
        a += 1
    else:
        pass

print('Number of acquisitions is {}.'.format(a))


In [ ]:
#Repetitions counter
#import collections
#counter=collections.Counter(Aonly_rounds_energy_date['company_name'])
#print(counter.most_common(46)) #there are 46 in total, ranging from 4 A rounds to 2.

In [ ]:
import collections
counter=collections.Counter(counter)
print(counter.most_common(460)) #there are 46 in total, ranging from 4 A rounds to 2.


In [ ]:
import collections
counters=collections.Counter(countings)
print(counters.most_common(460)) #there are 46 in total, ranging from 4 A rounds to 2.


In [ ]:
#exporting to csv before filtering VC rounds
energy_companies_filtered_bydate_with_rounds.to_csv(r'Export.csv')

writer = pd.ExcelWriter('export.xlsx', engine='xlsxwriter')

# Write each dataframe to a different worksheet.
energy_companies_filtered_bydate_with_rounds.to_excel(writer, sheet_name='Founded')
rounds_energy_filtered_date.to_excel(writer, sheet_name='Rounds')

all_acquis.to_excel(writer, sheet_name='Acq')
all_ipos.to_excel(writer, sheet_name='Ipos')


# Close the Pandas Excel writer and output the Excel file.
writer.save()
